In [2]:
import json
from utils import handle_request
from tqdm import tqdm

Request the Beacon API to get all proposer violations.

In [ ]:
with open("slashed_validator.json", "r") as in_fd:
    slashed_validator = json.load(in_fd, )

unique_proposer_violations = {}
for item in slashed_validator:
    if item['reason'] == "Proposer Violation" and item['slot'] not in unique_proposer_violations:
        unique_proposer_violations[item['slot']] = {}
unique_proposer_violations_list = []
for key in unique_proposer_violations:
    unique_proposer_violations_list.append(str(key))

print(len(unique_proposer_violations_list))
for item in tqdm(unique_proposer_violations_list):
    data = handle_request("https://beaconcha.in/api/v1/block/{}/proposerslashings".format(item))
    unique_proposer_violations[int(item)] = data

with open("proposer_violation.json", "w") as out_fd:
    json.dump(unique_proposer_violations, out_fd, indent=4)

Draw proposer violations over time.

In [3]:
import plotly.express as px
import pandas as pd

with open("proposer_violation.json", "r") as fd:
    proposer_violations = json.load(fd)

slashed_epoch = {}
for e in range(0, 148720):
    slashed_epoch[e] = 0
    if str(e) in proposer_violations:
        slashed_epoch[e] += 1

df = pd.DataFrame.from_dict(slashed_epoch, orient='index', columns=['Proposer Violations'])
df['epoch'] = df.index
fig = px.histogram(df, x=df.epoch, y=df.columns[0],
                   title='Proposer Violations over Epoch', nbins=300)
fig.show()